### 0. Setup
- Clone https://github.com/plaggy/rag-gradio-sample-project and set up an environment with gradio_app/requirements.txt.

A convenient way to work through the project is to test locally and keep committing the changes to the [HF Spaces](https://huggingface.co/spaces) repo. A space gets automatically rebuilt after each commit and you get a new version of your application up and running.

- Create a new space with Gradio SDK. You'll get an almost empty repo, the only thing you'll need from it is README.md which has a config letting a space builder know that it's a Gradio app. Reset a remote upstream of your local rag-gradio-sample-project clone to be your freshly created Spaces repository.

The easiest way to set your space up is to set up the gradio_app folder as a git repo, set remote origin to your space repo and checkout the remote README:

```
cd gradio_app
git init
git remote add origin <your spaces repo url>
git fetch
git checkout origin/main README.md
```

The space is not working yet. You'll get the first working version after the Step 3.

- Clone https://github.com/huggingface/transformers to a local machine and run prep_scripts/markdown_to_text.py script to extract raw text from transformers/docs/source/en/. This will be your knowledge base, you don't need it to be a part of your repository

Run the command as follows (pass arguments that work for you)
```
python prep_scripts/markdown_to_text.py --input-dir transformers/docs/source/en/ --output-dir docs
```


**By design, you'll be running your experiments in a [Gradio space](https://huggingface.co/docs/hub/en/spaces-sdks-gradio). Apart from deliverables for each step you'll need to provide a link to a functioning RAG space in it final state!**

# Add the link to the space you've just created here: 
https://huggingface.co/spaces/petuch03/generative-ai-rag-project
All env variables are stored in setting of the Space, so you wont see .env file in the HG Space.

### Step 1: Chunk Your Data

To efficiently pull up documents relevant to a query from a knowledge base documents are embedded and stored as vectors. Documents in your knowledge base are not expected to fit into the context length of an embedding model (most have 512 token limit). Hence chunking your documents into smaller pieces is required. Take a deeper dive into why chunking is imoprtant and what are the options [here](https://www.pinecone.io/learn/chunking-strategies/).

Your task is to implement and compare two chunking strategies: fixed-sized chunking and content-aware chunking. For content-aware you could split by sentences, paragraphs or in some other way that makes sence.

The deliverables are:
- The code for chunk splitting

In [23]:
import nltk
nltk.download('punkt')

from langchain.text_splitter import CharacterTextSplitter, NLTKTextSplitter, RecursiveCharacterTextSplitter

def fixed_size_chunk(text):
    text_splitter = CharacterTextSplitter(
        separator = "\n\n",
        chunk_size = 256,
        chunk_overlap = 20
    )
    docs = text_splitter.create_documents([text])
    return docs

def content_aware_chunk_sentence(text):
    text_splitter = NLTKTextSplitter(
        chunk_size = 256,
        chunk_overlap = 20
    )
    docs = text_splitter.create_documents([text])
    return docs

def content_aware_chunk_paragraph(text):
    text_splitter = RecursiveCharacterTextSplitter(
        chunk_size = 1024,
        chunk_overlap = 50
    )
    docs = text_splitter.create_documents([text])
    return docs

[nltk_data] Downloading package punkt to /Users/es/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [19]:
text = open("docs/_accelerate.txt", "r").read()
print(fixed_size_chunk(text), end="\n====================\n")

[Document(page_content="Distributed training with 🤗 Accelerate\nAs models get bigger, parallelism has emerged as a strategy for training larger models on limited hardware and accelerating training speed by several orders of magnitude. At Hugging Face, we created the 🤗 Accelerate library to help users easily train a 🤗 Transformers model on any type of distributed setup, whether it is multiple GPU's on one machine or multiple GPU's across several machines. In this tutorial, learn how to customize your native PyTorch training loop to enable training in a distributed environment.\nSetup\nGet started by installing 🤗 Accelerate:"), Document(page_content="pip install accelerate\nThen import and create an [~accelerate.Accelerator] object. The [~accelerate.Accelerator] will automatically detect your type of distributed setup and initialize all the necessary components for training. You don't need to explicitly place your model on a device."), Document(page_content='from accelerate import Accele

In [20]:
import os

def preprocess_docs(input_folder, output_folder, chunk_method):
    if not os.path.exists(output_folder):
        os.makedirs(output_folder)

    for filename in os.listdir(input_folder):
        file_path = os.path.join(input_folder, filename)

        with open(file_path, 'r', encoding='utf-8') as file:
            content = file.read()

        chunks = chunk_method(content)

        for i, chunk in enumerate(chunks):
            chunk_filename = f"{filename}_chunk_{i+1}.txt"
            chunk_filepath = os.path.join(output_folder, chunk_filename)

            with open(chunk_filepath, 'w', encoding='utf-8') as chunk_file:
                chunk_file.write(chunk.page_content)

In [21]:
preprocess_docs("docs", "docs_content_aware_sentence", content_aware_chunk_sentence)

In [22]:
preprocess_docs("docs", "docs_fixed_size_chunk_splitting", fixed_size_chunk)

In [24]:
preprocess_docs("docs", "docs_content_aware_paragraph", content_aware_chunk_paragraph)

### Step 2: Ingest chunks into a database and create an index

Chunks need to be vectorized and made accessible to an LLM to enable semantic search with embedding models. A current industry standard is to use a vector database to store and retrieve texts both conveniently and efficiently. There are many products out there, we'll be using [LanceDB](https://lancedb.github.io/lancedb/). LanceDB is a young product, one way it stands out is that it's embedded - it's designed not to be a standalone service but rather a part of an application, more on this [here](https://lancedb.github.io/lancedb/basic/).

Find more details on how different databases compare in [this](https://thedataquarry.com/tags/vector-db/) series of posts. 

Your task is to vectorize and ingest chunked documents into the database. 
**For each chunking strategy from the previous step create a separate table with one of the embedding models. Compare the chunking strategies and choose one. Perform vectorization+ingestion with the second model only with one chunking strategy of your choice**.
Use prep_scrips/lancedb_setup.py to vectorize chunks and store vector representations along with raw text in a Lancedb instance. The script also creates an index for fast ANN retrieval (not really needed for this exercise but necessary at scale). Try different embedding models and see how results differ. The options are:

- `sentence-transformers/all-MiniLM-L6-v2`: a light model, produces vectors of length 384
- `BAAI/bge-large-en-v1.5`: a much heavier model, embedding vector length is 1024

Feel free to explore other embedding models and justify your choice.
For different embedding models and different chunking strategies create different tables in the database so you can easily switch between them and compare.

Run the embedding+ingestion script as follows, make sure to look into the script and go over the arguments. Note that the number of sub-vectors for indexing must be a divisor of the model embedding size.

```
python prep_scrips/lancedb_setup.py --emb-model <model name> --table <db table name> --input-dir <folder with chunked docs> --num-sub-vectors <a number which is a divisor of the embedding dim>
```

Before committing to your space set up environment variables on the settings tab of your space, use `.env` as a ference list of all the things you can customize. Make sure to add HF_TOKEN and OPENAI_API_KEY as secrets.
Not all the parameters are required to set via environment variables, most have default values.

*The database is expected to be in the `gradio_app` folder under `.lancedb`, make sure to move it there if was initialized elsewhere.* It can be parametrized but it's unnecessary here.

To commit large files to Github use `git lfs`:
```
git lfs install
git lfs track "*.lance"
git lfs track "*.idx"
git add .gitattributes
```
Then proceed as usual.

For experimenting you can easily switch between embedding models/tables by changing the values of the corresponding env variables in your space (`EMB_MODEL`, `TABLE_NAME`). Overall, every time you change the value of an environment variable a space gets automatically rebuilt.

The deliverables are:
1. The illustration of how retrieved documents differ depending on the embedding model and the chunking strategy. You should create at least 3 tables: model_1 + chunking_strategy_1, model_1 + chunking_strategy_2, model_2 + chunking_strategy_<1 or 2>
2. The analysis of pros and cons of chunking strategies
3. The analysis of how retrieved document differ between embedding models (is one better than the other?)
4. The analysis of how the embedding time differs between models

Model 1, content aware chunking

In [10]:
!python3 /Users/es/Desktop/ml-playground/generative-ai-rag-project/prep_scripts/lancedb_setup.py --emb-model sentence-transformers/all-MiniLM-L6-v2 --db-loc /Users/es/Desktop/ml-playground/generative-ai-rag-project/.lancedb --table docs_content_aware_sentence --input-dir docs_content_aware_sentence

/Library/Python/3.9/site-packages/urllib3/__init__.py:34: NotOpenSSLWarning: urllib3 v2 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compiled with 'LibreSSL 2.8.3'. See: https://github.com/urllib3/urllib3/issues/3020
  warnings.warn(
INFO:sentence_transformers.SentenceTransformer:Load pretrained SentenceTransformer: sentence-transformers/all-MiniLM-L6-v2
/Users/es/Library/Python/3.9/lib/python/site-packages/torch/_utils.py:831: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  return self.fget.__get__(instance, owner)()
INFO:sentence_transformers.SentenceTransformer:Use pytorch device_name: mps
INFO:__main__:using mps device
[2024-02-21T11:10:05Z WARN  lance::dataset] No existing dataset at /Users/es/Desktop/ml-playground/generative-ai-ra

Model 1, fixed size chunking

In [13]:
!python3 /Users/es/Desktop/ml-playground/generative-ai-rag-project/prep_scripts/lancedb_setup.py --emb-model sentence-transformers/all-MiniLM-L6-v2 --db-loc /Users/es/Desktop/ml-playground/generative-ai-rag-project/.lancedb --table docs_fixed_size_chunk_splitting --input-dir docs_fixed_size_chunk_splitting

/Library/Python/3.9/site-packages/urllib3/__init__.py:34: NotOpenSSLWarning: urllib3 v2 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compiled with 'LibreSSL 2.8.3'. See: https://github.com/urllib3/urllib3/issues/3020
  warnings.warn(
INFO:sentence_transformers.SentenceTransformer:Load pretrained SentenceTransformer: sentence-transformers/all-MiniLM-L6-v2
/Users/es/Library/Python/3.9/lib/python/site-packages/torch/_utils.py:831: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  return self.fget.__get__(instance, owner)()
INFO:sentence_transformers.SentenceTransformer:Use pytorch device_name: mps
INFO:__main__:using mps device
Batches: 100%|████████████████████████████████████| 1/1 [00:00<00:00, 36.53it/s]

Batches: 100%|███████████████████

Model 2, content aware chunking

In [17]:
!python3 /Users/es/Desktop/ml-playground/generative-ai-rag-project/prep_scripts/lancedb_setup.py --emb-model BAAI/bge-large-en-v1.5 --db-loc /Users/es/Desktop/ml-playground/generative-ai-rag-project/.lancedb --table docs_large_model_content_aware_sentence --input-dir docs_content_aware_sentence --num-sub-vectors 1024

/Library/Python/3.9/site-packages/urllib3/__init__.py:34: NotOpenSSLWarning: urllib3 v2 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compiled with 'LibreSSL 2.8.3'. See: https://github.com/urllib3/urllib3/issues/3020
  warnings.warn(
INFO:sentence_transformers.SentenceTransformer:Load pretrained SentenceTransformer: BAAI/bge-large-en-v1.5
INFO:sentence_transformers.SentenceTransformer:Use pytorch device_name: mps
INFO:__main__:using mps device
Batches: 100%|████████████████████████████████████| 1/1 [00:00<00:00, 14.04it/s]

Batches: 100%|████████████████████████████████████| 1/1 [00:00<00:00, 14.69it/s]

Batches: 100%|████████████████████████████████████| 1/1 [00:00<00:00, 13.62it/s]

Batches: 100%|████████████████████████████████████| 1/1 [00:00<00:00, 14.76it/s]

Batches: 100%|████████████████████████████████████| 1/1 [00:00<00:00, 14.24it/s]

Batches: 100%|████████████████████████████████████| 1/1 [00:00<00:00, 13.54it/s]

Batches: 100%|███████████████████████████████

Model 2, content aware chunking by paragraph

In [25]:
!python3 /Users/es/Desktop/ml-playground/generative-ai-rag-project/prep_scripts/lancedb_setup.py --emb-model BAAI/bge-large-en-v1.5 --db-loc /Users/es/Desktop/ml-playground/generative-ai-rag-project/.lancedb --table docs_large_model_content_aware_paragraph --input-dir docs_content_aware_paragraph --num-sub-vectors 1024

/Library/Python/3.9/site-packages/urllib3/__init__.py:34: NotOpenSSLWarning: urllib3 v2 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compiled with 'LibreSSL 2.8.3'. See: https://github.com/urllib3/urllib3/issues/3020
  warnings.warn(
INFO:sentence_transformers.SentenceTransformer:Load pretrained SentenceTransformer: BAAI/bge-large-en-v1.5
INFO:sentence_transformers.SentenceTransformer:Use pytorch device_name: mps
INFO:__main__:using mps device
[2024-02-21T21:12:53Z WARN  lance::dataset] No existing dataset at /Users/es/Desktop/ml-playground/generative-ai-rag-project/.lancedb/docs_large_model_content_aware_paragraph.lance, it will be created
100%|███████████████████████████████████████| 1649/1649 [20:18<00:00,  1.35it/s]


#### Report

##### Chunking
Content-Aware Chunking by Sentence:
Pros:
- Sentences often contain a single idea or concept, leading to more precise embeddings for specific queries
- Avoiding the mixing of unrelated ideas

Cons:
- More chunks, what results in increasing indexing and retrieval times
- Important context or meaning that is spread over several sentences could be lost


Content-Aware Chunking by Paragraph:
Pros:
- Paragraphs typically encompass a complete thought or argument, capturing more context than individual sentences
- Less chunks, improving manageability and retrieval efficiency

Cons:
- Paragraphs can vary significantly in length, leading to inconsistent embedding quality
- Large paragraphs might still mix unrelated ideas, diluting the precision of embeddings


Fixed Size Chunking:
Pros:
- Ensures consistent chunk sizes, simplifying the processing pipeline
- Easier to manage and index due to predictability in chunk size

Cons:
- Arbitrary cuts can disrupt meaningful textual boundaries, harming the quality of embeddings
- Does not adapt to the natural structure of the content, possibly leading to non optimal representations

##### Embedding models
Sentence-Transformers/all-MiniLM-L6-v2:
Pros:
- Lighter model with faster embedding times, suitable for real-time applications

Cons:
- Shorter vector lengths might miss nuanced differences between closely related documents
- May not capture the complexity of very specific or technical queries as effectively

Time consumption:
- This model is designed for efficiency and speed, with its lower-dimensional embeddings (384-length vectors) allowing for quicker computation. Its lighter architecture enables faster embedding generation, making it suitable for applications requiring real-time responses or processing large datasets.

BAAI/bge-large-en-v1.5:
Pros:
- Longer embedding vectors capture more detail, potentially improving match quality for complex queries
- Better at distinguishing between closely related documents due to the higher dimensional space

Cons:
- Slower embedding times, making it less suitable for real-time applications
- Requires more memory and computational power

Time consumption:
- Being a "heavier" model with longer embedding vectors (1024-length vectors), it inherently requires more computation per embedding. This results in longer embedding times compared to lighter models. However, representation ability of this model is a head above the small 384-length model.

### Step 3: Add a reranker

A reranker is a second-level model which produces similarity scores for pairs of (input query + retrieved document). Cross-encoders are conventionally used for reranking, their architecture is slightly different from retrieval models (more on it [here] and [here](https://www.sbert.net/examples/applications/retrieve_rerank/README.html)). Cross-encoders are much more costly to run, therefore a retrieval model is used to get a few (dozens) highest-scoring items, and a reranker picks the best among these. The overall pipeline is similar to the recommender system industry standard: a light model retrieves top-n, a precise and heavy model reranks n to get top k, n is orders of magnitude larger than k.

Cross-encoders are optional because of the overhead their usage implies. Your task is to implement a reranker using a cross-encoder and assess pros and cons of having it. Do not forget that the process of pulling the most relevant documents becomes two-staged: retrieve a larger number of items first, than rerank and keep the best top-k for context.

The models fit for the task:
1. BAAI/bge-reranker-large
2. cross-encoder/ms-marco-MiniLM-L-6-v2

As usual, feel free to pick another model and provide some description to it.

The deliverables are:

1. The code that enables a reranker.
2. A comparison of how the prompt and the model output change after adding a reranker
3. The analysis of pros and cons. The evaluation aspects should include the relevance of the top-k documents, the response time.


In [ ]:
# Implement code for selecting the final documents using a cross-encoder and compare with and without
from sentence_transformers import CrossEncoder
import numpy as np
import logging


CROSS_ENCODER = os.getenv("CROSS_ENCODER")
cross_encoder = CrossEncoder(CROSS_ENCODER)

logging.basicConfig(level=logging.INFO)
retrieve_logger = logging.getLogger(__name__)

def rerank(query, documents, k):
    retrieve_logger.info(f"Rerank in progress, reduced {len(documents)} retrieved documents to {k}")
    pairs = [[query, doc] for doc in documents]
    scores = cross_encoder.predict(pairs)
    sorted_indices = np.argsort(scores)[::-1]
    top_k_documents = [documents[index] for index in sorted_indices[:k]]
    retrieve_logger.info("Rerank successfully completed.")
    return top_k_documents

`BAAI/bge-reranker-large` (on the local machine) timing is presented below. The timing on HG Space is worse, why -- I am still trying to figure out
```
INFO:__main__:Retrieving documents...
Batches: 100%|██████████| 1/1 [00:00<00:00,  1.89it/s]
INFO:backend.semantic_search:Rerank in progress, reduced 10 retrieved documents to 5
Batches: 100%|██████████| 1/1 [00:10<00:00, 10.14s/it]
INFO:backend.semantic_search:Rerank successfully completed.
INFO:__main__:Finished Retrieving documents in 10.7 seconds...
```
Reranker is good to use with many retrieved documents on the first step, and eliminating them during reranking. This is exactly what I did, i am retrieving 10 document before rerank and reduce their number to 5 during reranking.
Pros:
- More precise and relevant documents.
- Good to work with complex and big document database.

Cons:
- Much longer response time, and this is not what we want on such small knowledge base.


My opinion: on this database, reranker is unnecessary. On the bigger ones, its advantage will be more obdvious.

### Step 4: Try a different LLM

The suggested `Mistral-7b-instruct` is a great but small model for an LLM. A larger model can be applied to a wider range of problems and do more complex reasoning. Within the scope of this project a larger model may not be beneficial but for more complex cases the difference would become apparent. Another dimension to explore is a base model which was not instruction fine-tuned - it won't respond to your queries the way you'd expect. It may be a great exercise to see the value of fine-tuning.

The task here is to try out an alternative LLM to explore the differences.

The options are:
1. mistralai/Mistral-7B-v0.1
2. mistralai/Mixtral-8x7B-Instruct-v0.1

Of course, feel free to choose another one and give some details on how different it is from the initial model.

The deliverables are:

1. The comparison between outputs of the Mistral-7b-instuct and a different model of your choice.
2. The difference in response times if a larger model was chosen. Make sure to make multiple queries to make the comparison meaningful.
3. Analyse the differences between outputs and share the conclusions.

#### Analysis of the difference between LLMs
Everything was measured with reranking and on the same vector table.
```
| Question                                       | gpt-4-turbo-preview | mistralai/Mistral-7B-Instruct-v0.2 | mistralai/Mixtral-8x7B-Instruct-v0.1 |
|------------------------------------------------|---------------------|------------------------------------|--------------------------------------|
| Where does Philipp live?                       | 10.8s               | 11.6s                              | 11.9s                                |
| Does Germany have more than 50 million people? | 2.4s                | 2.4s                               | 3.7s                                 |
| How many people live in France?                | 2.8s                | 1.6s                               | 2.8s                                 |
```

The most time-consuming part is retrieval, models operate almost at the same speed. However, gpt-4-turbo-preview generate more precise and brief answers, which are more convenient to read. Both tested Mistral models are stating that they retrieved this information, so the reply with a long message to a very short and precise question.

Personally I would prefer to use gpt-4-turbo-preview over both Mistral models. But Mistrals indeed have their own advantages, such as relatively small amount of parameters. 

### Step 5 (Bonus): Use an LLM to quantitatively compare outputs of different variants of the system (LLM as a Judge)

Use a powerful LLM (e.g. GPT-4) to quantitatively evaluate outputs of two alternative setups (different embedding models, different LLMs, both etc.). For inspiration and for prompts refer to [1](https://arxiv.org/pdf/2306.05685.pdf), [2](https://arxiv.org/pdf/2401.10020.pdf), [3](https://www.airtrain.ai/blog/the-comprehensive-guide-to-llm-evaluation#high-level-approach)

The deliverables:

1. The code you put together
2. The high-level description of the setup
3. The results of the qualitative comparison


In [2]:
# The code implementing LLM-as-a-Judge and the evaluation results